In [ ]:
import os
import sys
import torch
need_pytorch3d=False
try:
    import pytorch3d
except ModuleNotFoundError:
    need_pytorch3d=True
if need_pytorch3d:
    if torch.__version__.startswith("1.10.") and sys.platform.startswith("linux"):
        # We try to install PyTorch3D via a released wheel.
        pyt_version_str=torch.__version__.split("+")[0].replace(".", "")
        version_str="".join([
            f"py3{sys.version_info.minor}_cu",
            torch.version.cuda.replace(".",""),
            f"_pyt{pyt_version_str}"
        ])
        !pip install fvcore iopath
        !pip install --no-index --no-cache-dir pytorch3d -f https://dl.fbaipublicfiles.com/pytorch3d/packaging/wheels/{version_str}/download.html
    else:
        # We try to install PyTorch3D from source.
        !curl -LO https://github.com/NVIDIA/cub/archive/1.10.0.tar.gz
        !tar xzf 1.10.0.tar.gz
        os.environ["CUB_HOME"] = os.getcwd() + "/cub-1.10.0"
        !pip install 'git+https://github.com/facebookresearch/pytorch3d.git@stable'

In [ ]:
# Set up starter code
!git clone https://github.com/learning3d/assignment1.git
!mv assignment1/* .
!pip install -r requirements.txt

Cloning into 'assignment1'...
remote: Enumerating objects: 46, done.
remote: Counting objects: 100% (46/46), done.
remote: Compressing objects: 100% (36/36), done.
remote: Total 46 (delta 9), reused 40 (delta 7), pack-reused 0
Unpacking objects: 100% (46/46), done.
     |████████████████████████████████| 265 kB 4.3 MB/s 


In [ ]:
import cv2
import matplotlib.pyplot as plt
import numpy as np
import pytorch3d
import pytorch3d.io
from pytorch3d.vis.plotly_vis import plot_scene
from tqdm.auto import tqdm

import starter.utils

In [ ]:
# This should print True if you are using your GPU
print("Using GPU:", torch.cuda.is_available())
if torch.cuda.is_available():
    device = torch.device("cuda:0")
else:
    device = torch.device("cpu")

Using GPU: True


In [ ]:
vertices, face_props, text_props = pytorch3d.io.load_obj("data/cow.obj")
faces = face_props.verts_idx
print("Vertices", vertices.shape)
print("Faces", faces.shape)

Vertices torch.Size([2930, 3])
Faces torch.Size([5856, 3])


In [ ]:
# All Pytorch3D elements need to be batched!
vertices = vertices.unsqueeze(0)  # 1 x N_v x 3
faces = faces.unsqueeze(0)  # 1 x N_f x 3

#print("Vertices", vertices.shape)
#print("Faces", faces.shape)
texture_rgb = torch.ones_like(vertices)
texture_rgb = texture_rgb * torch.tensor([0.7, 0.7, 1])
textures = pytorch3d.renderer.TexturesVertex(texture_rgb)
#print(texture_rgb)
#print(texture_rgb.shape)

meshes = pytorch3d.structures.Meshes(
    verts=vertices,
    faces=faces,
    textures=textures,
)
meshes = meshes.to(device)  # Move mesh to GPU
#print(meshes.verts_padded().shape)
#print(meshes.faces_padded().shape)

In [ ]:
# Camera orientation setup
R = torch.eye(3).unsqueeze(0)
T = torch.tensor([[0, 0, 3]])
cameras = pytorch3d.renderer.FoVPerspectiveCameras(
    R=R,
    T=T,
    fov=60,
    device=device,
)
cameras.get_camera_center()
transform = cameras.get_world_to_view_transform()
transform.get_matrix()

tensor([[[1., 0., 0., 0.],
         [0., 1., 0., 0.],
         [0., 0., 1., 0.],
         [0., 0., 3., 1.]]], device='cuda:0')

In [ ]:
# Renderer setup/parameter
image_size = 512

raster_settings = pytorch3d.renderer.RasterizationSettings(image_size=image_size)
rasterizer = pytorch3d.renderer.MeshRasterizer(
    raster_settings=raster_settings,
)
shader = pytorch3d.renderer.HardPhongShader(device=device)
renderer = pytorch3d.renderer.MeshRenderer(
    rasterizer=rasterizer,
    shader=shader,
)

In [ ]:
# imge parameter
image = renderer(meshes, cameras=cameras)
print(image.shape)
image = image[0].cpu().numpy()
plt.imshow(image)

#light parameter
lights = pytorch3d.renderer.PointLights(location=[[0, 0, -3]], device=device)
image = renderer(meshes, cameras=cameras, lights=lights)
'''
plt.imshow(image[0].cpu().numpy())
plot_scene({
    "figure": {
        "Mesh": meshes,
        "Camera": cameras,
    }
})
'''

P1: 360 View

To generate 360 views, execute all code blocks above. If there is a issue with GPU, then select select NONE in the option for additonal power

In [ ]:
num_views = 15
R_gif, T_gif = pytorch3d.renderer.look_at_view_transform(
    dist=3,
    elev=0,
    azim=np.linspace(-180, 180, num_views, endpoint=False),
)
#print("R_gif", R_gif.shape)
#print("T_gif", T_gif.shape)
many_cameras = pytorch3d.renderer.FoVPerspectiveCameras(
    R=R_gif,
    T=T_gif,
    device=device
)
images_gif = renderer(meshes.extend(num_views), cameras=many_cameras, lights=lights)
my_images=[]
for i, image in enumerate(images_gif):
    #print(image.shape)
    temp=image.cpu().detach().numpy()
    my_images.append(temp)
    #print(type(temp))

#print(type(my_images))
import imageio
imageio.mimsave('P1.gif', my_images, fps=15)

P 1.2 Dolly zoom, for this problem, just run the code block below and it should be enough

In [ ]:
import argparse

import imageio
import numpy as np
import pytorch3d
import torch
from PIL import Image, ImageDraw
from tqdm.auto import tqdm

from starter.utils import get_device, get_mesh_renderer

import math

image_size=256
num_frames=10
duration=3
device=None
output_file="dolly.gif"

if device is None:
    device = get_device()

mesh = pytorch3d.io.load_objs_as_meshes(["data/cow_on_plane.obj"])
mesh = mesh.to(device)
renderer = get_mesh_renderer(image_size=image_size, device=device)
lights = pytorch3d.renderer.PointLights(location=[[0.0, 0.0, -3.0]], device=device)

fovs = torch.linspace(5, 120, num_frames)

renders = []
temp=70*math.tan(5/2/180*math.pi)
#print('temp',temp)
for fov in tqdm(fovs):
    distance = temp/math.tan(fov/2/180*math.pi) 
    #print('distance',distance,'angle tan',math.tan(fov/2/180*math.pi))
    T = [[0, 0, distance]]
    cameras = pytorch3d.renderer.FoVPerspectiveCameras(fov=fov, T=T, device=device)
    rend = renderer(mesh, cameras=cameras, lights=lights)
    rend = rend[0, ..., :3].cpu().numpy()  # (N, H, W, 3)
    renders.append(rend)
    
images = []
for i, r in enumerate(renders):
    image = Image.fromarray((r * 255).astype(np.uint8))
    draw = ImageDraw.Draw(image)
    draw.text((20, 20), f"fov: {fovs[i]:.2f}", fill=(255, 0, 0))
    images.append(np.array(image))
    imageio.mimsave(output_file, images, fps=(num_frames / duration))


  0%|          | 0/10 [00:00<?, ?it/s]

P2.1 Constructing a Tetrahedron, just run the following three codeblocks in sequence should be enough, the output is P2_1.gif

In [ ]:
import argparse
import matplotlib.pyplot as plt
import pytorch3d
import torch
from starter.utils import get_device, get_mesh_renderer, load_cow_mesh

#cow_path="data/cow.obj" 
image_size=256
color=[0.7, 0.7, 1]
device=None    
if device is None:
    device = get_device()

# Get the renderer.
renderer = get_mesh_renderer(image_size=image_size)

vertices_tara = np.array([[0,0,0],[-0.3,0.3,0],[0.3,0.3,0],[0,0.3,0.3]])
faces_tara = np.array([[1,0,2],[2,0,3],[3,0,1],[1,2,3]])

#vertices_tara=vertices_tara.astype('double')
#faces_tara=faces_tara.astype('double')

vertices_tara=torch.from_numpy(vertices_tara).float()
faces_tara=torch.from_numpy(faces_tara).float()

#vertices_tara=vertices_tara.type(torch.DoubleTensor)
#faces_tara=faces_tara.type(torch.DoubleTensor)

vertices_tara = vertices_tara.unsqueeze(0) 
faces_tara = faces_tara.unsqueeze(0)  

#print('vertices_tara shape',vertices_tara.shape)
#print('vertices_tara type',type(vertices_tara[0]))
#print('vertices_tara[0]',vertices_tara[0][0])
#print('faces_tara shape',faces_tara.shape)
#print('faces_tara[0]',faces_tara[0][0])

textures = torch.ones_like(vertices_tara)  # (1, N_v, 3)
textures = textures * torch.tensor(color)  # (1, N_v, 3)
mesh_tara = pytorch3d.structures.Meshes(
    verts=vertices_tara,
    faces=faces_tara,
    textures=pytorch3d.renderer.TexturesVertex(textures),
    )

In [ ]:
#image test
mesh = mesh_tara.to(device)

    # Prepare the camera:
cameras = pytorch3d.renderer.FoVPerspectiveCameras(
    R=torch.eye(3).unsqueeze(0), T=torch.tensor([[0, 0, 1.5]]), fov=60, device=device
)

# Place a point light in front of the cow.
lights = pytorch3d.renderer.PointLights(location=[[0, 0, 0]], device=device)

rend = renderer(mesh, cameras=cameras, lights=lights)
rend = rend.cpu().numpy()[0, ..., :3] 
'''
plt.imsave('P2_1.jpg', rend) 
plot_scene({
    "figure": {
        "Mesh": mesh_tara,
        "Camera": cameras,
    }
})
'''

In [ ]:
mesh = mesh_tara.to(device)
lights = pytorch3d.renderer.PointLights(location=[[0, 3, 0]], device=device)

num_views = 15
R_gif, T_gif = pytorch3d.renderer.look_at_view_transform(
    dist=1.5,
    elev=3,
    azim=np.linspace(-180, 180, num_views, endpoint=False),
)
#print("R_gif", R_gif.shape)
#print("T_gif", T_gif.shape)
many_cameras = pytorch3d.renderer.FoVPerspectiveCameras(
    R=R_gif,
    T=T_gif,
    device=device
)

images_gif = renderer(mesh.extend(num_views), cameras=many_cameras, lights=lights)
my_images=[]
for i, image in enumerate(images_gif):
    #print(image.shape)
    temp=image.cpu().detach().numpy()
    my_images.append(temp)
    #print(type(temp))
import imageio
# output gif samples
#my_images = images_gif  # List of images [(H, W, 3)]
#print('my_images.shape',my_images.shape)
imageio.mimsave('P2_1.gif', my_images, fps=15)

P2_2 Cube, to generate, run the following codeblock is enough

In [ ]:
import argparse
import matplotlib.pyplot as plt
import pytorch3d
import torch
from starter.utils import get_device, get_mesh_renderer, load_cow_mesh

image_size=256
color=[0.7, 0.7, 1]
device=None    
if device is None:
    device = get_device()

# Get the renderer.
renderer = get_mesh_renderer(image_size=image_size)

vertices_cube = np.array([[-1,-1,-1],[1,-1,-1],[1,-1,1],[-1,-1,1],
              [1,1,1],[-1,1,1],[-1,1,-1],[1,1,-1]])
faces_cube = np.array([[6,0,1],[6,7,1],[7,1,4],[1,2,4],
            [4,2,5],[2,3,5],[5,3,0],[6,0,5],
            [5,6,7],[5,4,7],[3,0,1],[3,2,1]])

vertices_cube=torch.from_numpy(vertices_cube).float()
faces_cube=torch.from_numpy(faces_cube).float()

vertices_cube = vertices_cube.unsqueeze(0) 
faces_cube = faces_cube.unsqueeze(0)  

textures = torch.ones_like(vertices_cube)  # (1, N_v, 3)
textures = textures * torch.tensor(color)  # (1, N_v, 3)
mesh_cube = pytorch3d.structures.Meshes(
    verts=vertices_cube,
    faces=faces_cube,
    textures=pytorch3d.renderer.TexturesVertex(textures),
    )

mesh = mesh_cube.to(device)
lights = pytorch3d.renderer.PointLights(location=[[0, 3, 0]], device=device)

num_views = 20
R_gif, T_gif = pytorch3d.renderer.look_at_view_transform(
    dist=5,
    elev=3,
    azim=np.linspace(-180, 180, num_views, endpoint=False),
)
#print("R_gif", R_gif.shape)
#print("T_gif", T_gif.shape)
many_cameras = pytorch3d.renderer.FoVPerspectiveCameras(
    R=R_gif,
    T=T_gif,
    device=device
)

images_gif = renderer(mesh.extend(num_views), cameras=many_cameras, lights=lights)
my_images=[]
for i, image in enumerate(images_gif):
    #print(image.shape)
    temp=image.cpu().detach().numpy()
    my_images.append(temp)
    #print(type(temp))
import imageio
# output gif samples
#my_images = images_gif  # List of images [(H, W, 3)]
#print('my_images.shape',my_images.shape)
imageio.mimsave('P2_2.gif', my_images, fps=15)

P3 Texture color, to generate, run the following codeblock. The color1 is pure blue, and color2 is pure red based on matrix [R,G,B]

In [ ]:
import argparse

import matplotlib.pyplot as plt
import pytorch3d
import torch

from starter.utils import get_device, get_mesh_renderer, load_cow_mesh

image_size=256

#color=[0.7, 0.7, 1]


device=None
if device is None:
  device = get_device()

renderer = get_mesh_renderer(image_size=image_size)
vertices, faces = load_cow_mesh("data/cow.obj")
vertices = vertices.unsqueeze(0)  # (N_v, 3) -> (1, N_v, 3)
faces = faces.unsqueeze(0)  # (N_f, 3) -> (1, N_f, 3)
textures = torch.ones_like(vertices)  # (1, N_v, 3)

#print('vertices',vertices.shape)
#print('vertices[0]',vertices[0][:,2])
zmin = min(vertices[0][:,2])
zmax = max(vertices[0][:,2])
#print(zmin,zmax)
color1 = np.array([[0,0,1]])
color2 = np.array([[1,0,0]])
#print(color1.shape)

texture=np.zeros((vertices.shape[1],3))
for i in range(vertices.shape[1]):
  z = vertices[0][i,2]
  alpha = (z - zmin) / (zmax - zmin)
  color = alpha * color2 + (1 - alpha) * color1
  texture[i,:]=color[:]
  #np.vstack((texture,color))
texture =np.array([texture])
texture=torch.from_numpy(texture).float()
texture.squeeze(0)
#print('texture type',type(texture))
#print('texture shape',texture.shape)
#print('texture color',texture[0])
#side image view
#extures = textures * torch.tensor(color)  # (1, N_v, 3)
textures = texture
mesh = pytorch3d.structures.Meshes(
    verts=vertices,
    faces=faces,
    textures=pytorch3d.renderer.TexturesVertex(textures),
)
mesh = mesh.to(device)


relative_rotation = pytorch3d.transforms.euler_angles_to_matrix(
    torch.tensor([0, np.pi/2, 0]), "XYZ"
)
#R=torch.eye(3).unsqueeze(0)
# Prepare the camera:
cameras = pytorch3d.renderer.FoVPerspectiveCameras(
    R=relative_rotation.unsqueeze(0), T=torch.tensor([[0, 0, 3]]), fov=60, device=device
)

    # Place a point light in front of the cow.
lights = pytorch3d.renderer.PointLights(location=[[0, 0, -3]], device=device)

rend = renderer(mesh, cameras=cameras, lights=lights)
rend = rend.cpu().numpy()[0, ..., :3]
#plt.imsave('P3.jpg', rend)
#360 rotation view
num_views = 20
R_gif, T_gif = pytorch3d.renderer.look_at_view_transform(
    dist=5,
    elev=3,
    azim=np.linspace(-180, 180, num_views, endpoint=False),
)
#print("R_gif", R_gif.shape)
#print("T_gif", T_gif.shape)
many_cameras = pytorch3d.renderer.FoVPerspectiveCameras(
    R=R_gif,
    T=T_gif,
    device=device
)

images_gif = renderer(mesh.extend(num_views), cameras=many_cameras, lights=lights)
my_images=[]
for i, image in enumerate(images_gif):
    #print(image.shape)
    temp=image.cpu().detach().numpy()
    my_images.append(temp)
    #print(type(temp))
import imageio
# output gif samples
#my_images = images_gif  # List of images [(H, W, 3)]
#print('my_images.shape',my_images.shape)
imageio.mimsave('P3.gif', my_images, fps=15)

P4 Rotate based on axis. To generate the picture with different roation, coment out the section in the code

In [ ]:
import argparse

import matplotlib.pyplot as plt
import pytorch3d
import torch

from starter.utils import get_device, get_mesh_renderer


def render_textured_cow(
    cow_path="data/cow.obj",
    image_size=256,
    R_relative=[[1, 0, 0], [0, 1, 0], [0, 0, 1]],
    T_relative=[0, 0, 0],
    device=None,
):
    if device is None:
        device = get_device()
    meshes = pytorch3d.io.load_objs_as_meshes([cow_path]).to(device)
    '''
    R_relative=[[1, 0, 0], [0, 1, 0], [0, 0, 1]]
    T_relative=[0, 0, 0]
    '''

    '''
    #rotate around x
    a=torch.FloatTensor([1*3.1415/2])
    R_relative=[[1.0, 0, 0], 
          [0, torch.cos(a), -torch.sin(a)], 
          [0, torch.sin(a), torch.cos(a)]]
    T_relative=[0.0, 0, 0] 
    '''

    '''
    #rotate around y
    a=torch.FloatTensor([3.1415/2])
    R_relative =[[torch.cos(a), 0, torch.sin(a)], 
           [0,1 ,0 ], 
           [-torch.sin(a),0 ,torch.cos(a) ]]
    T_relative=[0.0, 0, 3]
    '''
    #'''
    #rotate around z
    a=torch.FloatTensor([3.1415/2])
    R_relative = [[torch.cos(a), torch.sin(a),0 ], 
            [-torch.sin(a), torch.cos(a),0 ], 
            [0,0 ,1]]
    T_relative=[0.0, 0, 3]

    #'''


    R_relative = torch.tensor(R_relative).float()
    T_relative = torch.tensor(T_relative).float()
    R = R_relative @ torch.tensor([[1.0, 0, 0], [0, 1, 0], [0, 0, 1]])
    T = torch.tensor([0.0, 0, 3]) + T_relative
    
    
    renderer = get_mesh_renderer(image_size=256)
    cameras = pytorch3d.renderer.FoVPerspectiveCameras(
        R=R.unsqueeze(0), T=T.unsqueeze(0), device=device,
    )
    lights = pytorch3d.renderer.PointLights(location=[[0, 0.0, -3.0]], device=device,)
    rend = renderer(meshes, cameras=cameras, lights=lights)
    return rend[0, ..., :3].cpu().numpy()


render_textured_cow(cow_path="data/cow.obj", image_size=256)
plt.imsave('textured_cow_1.jpg', render_textured_cow())
